In [ ]:
# ! uv pip install E:\Work\ruzt\msyrs --upgrade

### Import Python packages


In [ ]:
import macrosynergy
import pandas as pd
import numpy as np
import polars as pl
import os

from macrosynergy.panel import view_timelines
from macrosynergy.management.types import QuantamentalDataFrame


### Import Python bindings - `msyrs`


In [ ]:
import msyrs

In [ ]:
DATA_FOLDER_PATH = "E:/Work/jpmaqs-data"
# DATA_FOLDER_PATH = "C:/Users/PalashTyagi/Code/go-dataquery/jpmaqs-data"
DQ_CLIENT_ID = os.getenv("DQ_CLIENT_ID")
DQ_CLIENT_SECRET = os.getenv("DQ_CLIENT_SECRET")

In [ ]:
import time

nb_start_time = time.time()

In [ ]:
dfpath = f"{DATA_FOLDER_PATH}/data/ADPEMPL_SA_P1M1ML1/USD_ADPEMPL_SA_P1M1ML1.csv"

starttime = time.time()
ldf: pl.DataFrame = msyrs.qdf.load_qdf(dfpath)
print(f"Time taken to load qdf: {time.time() - starttime}")
ldf.head(5)

In [ ]:
cids_dm = "AUD.CAD.CHF.EUR.GBP.JPY.NOK.NZD.SEK.USD".split(".")
cids_em = "CLP.COP.CZK.HUF.IDR.ILS.INR.KRW.MXN.PLN.THB.TRY.TWD.ZAR".split(".")
cids = cids_dm + cids_em
cids_dux = list(set(cids) - set(["IDR", "NZD"]))
ecos = (
    "CPIC_SA_P1M1ML12.CPIC_SJA_P3M3ML3AR.CPIC_SJA_P6M6ML6AR.CPIH_SA_P1M1ML12."
    "CPIH_SJA_P3M3ML3AR.CPIH_SJA_P6M6ML6AR.INFTEFF_NSA.INTRGDP_NSA_P1M1ML12_3MMA."
    "INTRGDPv5Y_NSA_P1M1ML12_3MMA.PCREDITGDP_SJA_D1M1ML12.RGDP_SA_P1Q1QL4_20QMA."
    "RYLDIRS02Y_NSA.RYLDIRS05Y_NSA.PCREDITBN_SJA_P1M1ML12".split(".")
)

mkts = (
    "DU02YXR_NSA.DU05YXR_NSA.DU02YXR_VT10.DU05YXR_VT10.EQXR_NSA.EQXR_VT10."
    "FXXR_NSA.FXXR_VT10.FXCRR_NSA.FXTARGETED_NSA.FXUNTRADABLE_NSA".split(".")
)
xcats = ecos + mkts

tickers = [f"{c}_{x}" for c in cids for x in xcats]

In [ ]:
starttime = time.time()

big_df: pl.DataFrame = msyrs.qdf.load_qdf_from_download_bank(
    folder_path=DATA_FOLDER_PATH,
    xcats=xcats,
)
print(f"Time taken to load qdf batch: {time.time() - starttime}")


In [ ]:
big_df.estimated_size("mb")

In [ ]:
starttime = time.time()

test_df = msyrs.qdf.reduce_dataframe(df=big_df, xcats=mkts)

print(f"Time taken to reduce qdf: {time.time() - starttime}")
print(test_df.estimated_size("mb"))
test_df = None

In [ ]:
sel_cids = ["USD", "EUR", "GBP", "AUD", "CAD", "CHF", "JPY", "INR"]
start = "2000-01-01"

In [ ]:
eq_xcats = [xc for xc in xcats if xc.startswith("EQ")]
starttime = time.time()

eq_df = msyrs.qdf.reduce_dataframe(
    df=big_df, cids=sel_cids, xcats=eq_xcats, start=start
)

print(f"Time taken to reduce qdf: {time.time() - starttime}")

In [ ]:
fx_xcats = [xc for xc in xcats if xc.startswith("FX")]

starttime = time.time()

fx_df = msyrs.qdf.reduce_dataframe(
    df=big_df, cids=sel_cids, xcats=fx_xcats, start=start
)
new_df: pl.DataFrame = msyrs.qdf.update_dataframe(df=eq_df, df_add=fx_df)

print(f"Time taken to reduce qdf: {time.time() - starttime}")

In [ ]:
starttime = time.time()

new_df: pl.DataFrame = msyrs.qdf.update_dataframe(df=eq_df, df_add=fx_df)

print(f"Time taken to update qdf: {time.time() - starttime}")

In [ ]:
msyrs.utils.get_bdates_series_default_opt(start_date='1971-01-01', end_date='2040-05-01', freq='D')

In [ ]:
msyrs.utils.get_bdates_series_default_pl(start_date='2000-01-01', end_date='2020-05-01', freq='D').dtype

In [ ]:
wdf = QuantamentalDataFrame(new_df.to_pandas()).to_wide()
# wdf.values[np.random.rand(*wdf.shape) < 0.0001] = np.nan
wdf = QuantamentalDataFrame.from_wide(wdf, categorical=False)
# cast column 'real_date' to pl.Date
new_df = pl.DataFrame(wdf).with_columns(
    pl.col("real_date").cast(pl.Date, strict=True)
)

In [ ]:
msyrs.utils.create_blacklist_from_qdf(new_df)

In [ ]:
view_timelines(df=new_df.to_pandas())

In [ ]:
end_time = time.time()
print(f"Time taken: {end_time - nb_start_time} seconds")